In [1]:
using LinearAlgebra, Plots

In [2]:
function householder_vector(x::Vector{<:AbstractFloat})::Tuple{Vector, AbstractFloat}
    # returns the normalized vector u such that H*x is a multiple of e_1

    s = norm(x)
    if x[1] ≥ 0
        s = -s
    end
    u = copy(x)
    u[1] -= s
    u ./= norm(u)
    return u, s
end

function householder_vector(x::Matrix{<:AbstractFloat})::Tuple{Matrix, AbstractFloat}
    # returns the normalized vector u such that H*x is a multiple of e_1

    s = norm(x)
    if x[1] ≥ 0
        s = -s
    end
    u = copy(x)
    u[1] -= s
    u ./= norm(u)
    return u, s
end

householder_vector (generic function with 2 methods)

In [3]:
x = [1., 2, 3]
householder_vector(x) |> display
x |> display

# better with copy and division in place
# @benchmark householder_vector(randn(100_000))

([0.7960091839647405, 0.3357514552548967, 0.503627182882345], -3.7416573867739413)

3-element Vector{Float64}:
 1.0
 2.0
 3.0

In [4]:
A = randn(5, 4)

# first step of QR factorization
R1 = A
(u1, s1) = householder_vector(R1[1:end,1])

H1 = I - 2 * u1 * u1'

Q1 = H1

Q1 * R1[1:end, 1] |> display # what we expect -> a multiple of e_1

5-element Vector{Float64}:
  3.983324158315414
 -5.457417586244235e-16
 -4.598436127585974e-17
 -1.4573782140540267e-16
  3.2867357162787514e-16

In [5]:
# second step
R2 = Q1 * R1

(u2, s2) = householder_vector(R2[2:end, 2])
H2 = I - 2 * u2 * u2'

# there is no blkdiag method in julia
# (maybe look into https://github.com/JuliaArrays/BlockDiagonals.jl)
# there are 2 methods (blocks is an array of blocks):
### METHOD 1:
# cat(blocks..., dims=(1,2))
### METHOD 2:
# using SparseArrays
# blockdiag(SparseMatrixCSC.(blocks)...)
## method 2 is slightly faster with subsequent matrix multiplication
# performance is ignored in this step
Q2 = cat(1, H2, dims=(1, 2))

Q2 * R2

5×4 Matrix{Float64}:
  3.98332      -1.23134       1.8182     0.590776
  3.80466e-16   1.52712      -1.85383   -0.709258
 -3.09958e-16  -1.11852e-17  -0.563749  -1.85235
  4.05338e-16  -4.61156e-17  -0.174643   1.27511
  1.55202e-16   1.4856e-17    1.73802    0.266999

In [6]:
# third step

R3 = Q2 * R2

(u3, s3) = householder_vector(R3[3:end, 3])
H3 = I - 2 * u3 * u3'

Q3 = cat(Diagonal(ones(2)), H3, dims=(1,2))
Q3 * R3

5×4 Matrix{Float64}:
  3.98332      -1.23134       1.8182        0.590776
  3.80466e-16   1.52712      -1.85383      -0.709258
  2.03593e-16   2.18903e-17   1.83549       0.700423
  4.4272e-16   -4.37079e-17   6.42625e-17   1.46093
 -2.16817e-16  -9.104e-18    -4.23002e-16  -1.58224

In [7]:
# fourth step

R4 = Q3 * R3

(u4, s4) = householder_vector(R4[4:end, 4])
H4 = I - 2 * u4 * u4'

Q4 = cat(Diagonal(ones(3)), H4, dims=(1,2))
Q4 * R4

# done because we arrived at the second dimension of A

5×4 Matrix{Float64}:
  3.98332      -1.23134       1.8182        0.590776
  3.80466e-16   1.52712      -1.85383      -0.709258
  2.03593e-16   2.18903e-17   1.83549       0.700423
 -4.5963e-16    2.29618e-17  -3.54379e-16  -2.15356
  1.78186e-16  -3.82887e-17  -2.39742e-16   1.50034e-16

In [8]:
function qrfactorization(A::Matrix{<:AbstractFloat})::Tuple{Matrix{<:AbstractFloat}, Matrix{<:AbstractFloat}}
    (m, n) = size(A)
    R = copy(A)
    Q = Diagonal(ones(eltype(A), m))

    for k ∈ 1:n
        (u, s) = householder_vector(R[k:end, k])
        # construct R
        R[k, k] = s
        R[k+1:end, k] .= 0
        R[k:end, k+1:end] -= 2 * u * (u' * R[k:end, k+1:end])
        # contruct the new H
        H = I - 2 * u * u'
        # contruct the Q
        Q = Q * cat(Diagonal(ones(eltype(A), k-1)), H, dims=(1,2)) # very inefficient (maybe simply send back the list of u_i)
    end
    return (Q, R)
end

qrfactorization (generic function with 1 method)

In [9]:
A = randn(Float32, 1000, 20)
(Q, R) = qrfactorization(A)
(norm(A - Q*R) ≤ size(A)[1] * 2^-23 * norm(A)) |> display
(norm(I - Q*Q') ≤ size(A)[1] * 2^-23) |> display

true

true